In [1]:
%pylab nbagg

Populating the interactive namespace from numpy and matplotlib


In [2]:
import glob
from collections import OrderedDict, namedtuple
import fabio, pyFAI
from pyFAI.geometryRefinement import GeometryRefinement
import os
from pyFAI.peak_picker import ControlPoints as _ControlPoints
Ellipse = namedtuple("Ellipse",["center_1", "center_2", "angle", "half_long_axis", "half_short_axis"])
from pyFAI.ext.marchingsquares import isocontour
from pyFAI.massif import Massif
from pyFAI.geometryRefinement import GeometryRefinement
from scipy.optimize import fmin_slsqp

In [3]:
#Re-implementation of the class: waiting 
class ControlPoints(_ControlPoints):
    def get_labels(self):
        """Retieve the list of labels 
        
        :return: list of labels as string  
        """
        labels = list(self._groups.keys())
        labels.sort(key=lambda item: self._groups[item].code)
        return labels
    
    def get(self, ring=None, lbl=None):
        """Retireves the last set of points for a given ring (by default the last)

        :param ring: index of ring to search for
        """
        out = None
        with self._sem:
            if lbl is None:
                if (ring is None):
                    lst = self.get_labels()
                    if not lst:
                        logger.warning("No group in ControlPoints.get")
                        return
                    lbl = lst[-1]
                else:
                    lst = [l for l, gpt in self._groups.items() if gpt.ring == ring]
                    lst.sort(key=lambda item: self._groups[item].code)
                    if not lst:
                        logger.warning("No group for ring %s in ControlPoints.get", ring)
                        return
                    lbl = lst[-1]
            if lbl in self._groups:
                out = self._groups.get(lbl)
            else:
                logger.warning("No such group %s in ControlPoints.pop", lbl)
        return out


In [ ]:
class SingleGeometry(object):
    def __init__(self, label, image=None, metadata=None, controlpoints=None, calibrant=None, geometryrefinement=None, function=None):
        self.label = label
        self.image = image
        self.metadata = metadata #may be anything
        self.controlpoints= controlpoints
        self.calibrant=calibrant
        self.geometryrefinement=geometryrefinement
        #self.function = 
        
    def get_position(self):
        """This method  is in charge of calculating the motor position from metadata/label/..."""
        #return float(self.metadata["motor_pos"].split()[0]) #D2AM
        return float(self.metadata.split("_")[1]) #ROBL

    def extract_cp(self, max_rings=None, pts_per_deg=1.0):
        """
        Performs an automatic keypoint extraction:
        Can be used in recalib or in calib after a first calibration has been performed.

        :param method: method for keypoint extraction
        :param pts_per_deg: number of control points per azimuthal degree (increase for better precision)
        """
        massif = Massif(self.image)
        tth = numpy.array([i for i in self.calibrant.get_2th() if i is not None])
        tth = numpy.unique(tth)
        tth_min = numpy.zeros_like(tth)
        tth_max = numpy.zeros_like(tth)
        delta = (tth[1:] - tth[:-1]) / 4.0
        tth_max[:-1] = delta
        tth_max[-1] = delta[-1]
        tth_min[1:] = -delta
        tth_min[0] = -delta[0]
        tth_max += tth
        tth_min += tth
        shape = self.image.shape
        ttha = self.geometryrefinement.twoThetaArray(shape)
        chia = self.geometryrefinement.chiArray(shape)
        rings = 0
        cp = ControlPoints(calibrant=self.calibrant)
        if max_rings is None:
            max_rings = tth.size
        for i in range(tth.size):
            if rings >= max_rings:
                break
            mask = numpy.logical_and(ttha >= tth_min[i], ttha < tth_max[i])
            if ai.detector.mask is not None:
                mask = numpy.logical_and(mask, numpy.logical_not(self.geometryrefinement.detector.mask))
            size = mask.sum(dtype=int)
            if (size > 0):
                rings += 1
                sub_data = self.image.ravel()[numpy.where(mask.ravel())]
                mean = sub_data.mean(dtype=numpy.float64)
                std = sub_data.std(dtype=numpy.float64)
                upper_limit = mean + std
                mask2 = numpy.logical_and(self.image > upper_limit, mask)
                size2 = mask2.sum(dtype=int)
                if size2 < 1000:
                    upper_limit = mean
                    mask2 = numpy.logical_and(self.image > upper_limit, mask)
                    size2 = mask2.sum()
                # length of the arc:
                points = isocontour(ttha, tth[i]).round().astype(int)
                seeds = set((i[1], i[0]) for i in points if mask2[i[1], i[0]])
                # max number of points: 360 points for a full circle
                azimuthal = chia[points[:, 1].clip(0, shape[0]), points[:, 0].clip(0, shape[1])]
                nb_deg_azim = numpy.unique(numpy.rad2deg(azimuthal).round()).size
                keep = int(nb_deg_azim * pts_per_deg)
                if keep == 0:
                    continue
                dist_min = len(seeds) / 2.0 / keep
                # why 3.0, why not ?

                print("Extracting datapoint for ring %s (2theta = %.2f deg); "
                            "searching for %i pts out of %i with I>%.1f, dmin=%.1f" %
                            (i, numpy.degrees(tth[i]), keep, size2, upper_limit, dist_min))
                res = massif.peaks_from_area(mask2, Imin=0, keep=keep, dmin=dist_min, seed=seeds, ring=i)
                cp.append(res, i)
        self.controlpoints = cp
        return cp        
    
    def display(self):
        if self.image is None:
            return
        fig= figure()
        ax = fig.add_subplot(1,1,1)
        ax.imshow(numpy.arcsinh(self.image), origin="lower")
        if self.controlpoints is not None:
            cp = self.controlpoints
            for i,lbl in enumerate(cp.get_labels()):
                pt = numpy.array(cp.get(lbl=lbl).points)
                ax.scatter(pt[:,1], pt[:,0], label=lbl)
            legend()
        if self.geometryrefinement is not None and self.calibrant is not None:
            ai = self.geometryrefinement
            tth = self.calibrant.get_2th()
            ttha = ai.twoThetaArray()
            ax.contour(ttha, levels=tth, cmap="autumn", linewidths=2, linestyles="dashed")
        return fig
        

In [ ]:
class MultiGeometryRefinement(object):
    def __init__(self):
        self.single_geometries = OrderedDict() # a dict of labels: SingleGeometry
        self.multiparam = [0.806, 4.55e-2, 4.62e-2, 0.0, 0.0, 1.0]
        #dist, poni1, poni2, rot1, offset2#, slope2
        self.bounds = [(0.6,0.9), #dist
                       (-0.1, 0.2), #poni1
                       (-0.1, 0.2), #poni2
                       (-0, 0), #rot1
                       (-0, 0), #offset
                       (1.0, 1.0), #slope
                      ]
    
    def new_geometry(self, label, image=None, metadata=None, controlpoints=None, calibrant=None, geometryrefinement=None):
        sg = SingleGeometry(label, image, metadata, controlpoints, calibrant, geometryrefinement)
        self.single_geometries[label] = sg
        return sg
    
    def __repr__(self):
        return "MultiGeometryRefinement with %i geometries labeled: %s"%(len(self.single_geometries), 
                                                                         " ".join(self.single_geometries.keys()))
    def translate(self, multiparam, motor_pos):
        """translate a set of param of the multigeometry into a paramter for SingleGeometry
        This is where the goniometer definition is
        """
        #return multiparam[0:3] + [numpy.radians(multiparam[4]*motor_pos+multiparam[3]), multiparam[5], numpy.pi/2.0]
        return numpy.concatenate((multiparam[0:4], [numpy.radians(motor_pos * multiparam[5] + multiparam[4]), 0]))
    
    def residu2(self, param):
        sumsquare = 0
        for key, single in self.single_geometries.items():
            motor_pos = single.get_position()
            single_param = self.translate(param, motor_pos)
            if single.geometryrefinement is not None and len(single.geometryrefinement.data):
                sumsquare += single.geometryrefinement.chi2(single_param)
        return sumsquare
    
    def chi2(self, param=None):
        if param is not None:
            return self.residu2(param)
        else:
            return self.residu2(self.multiparam)

    def refine2(self, maxiter=1000):
        self.multiparam = numpy.asarray(self.multiparam, dtype = numpy.float64)
        newparam = fmin_slsqp(self.residu2, self.multiparam, iter=maxiter,
                              iprint=2,bounds=self.bounds,
                              acc=1.0e-12)
        print(newparam)
        print("Constrained Least square", self.chi2(), "--> ", self.chi2(newparam))
        if self.chi2(newparam) < self.chi2():
            i = abs(self.multiparam - newparam).argmax()
            print("maxdelta on: ", i, self.multiparam[i], "-->", newparam[i])
            self.multiparam = newparam
        return self.multiparam

    def get_poni(self, lbl, motor_pos):
        r = self.translate(self.multiparam, motor_pos)
        gr = self.single_geometries[lbl].geometryrefinement
        ai = pyFAI.AzimuthalIntegrator(detector=gr.detector, wavelength=gr.wavelength)
        ai.dist = r[0]
        ai.poni1 = r[1]
        ai.poni2 = r[2]
        ai.rot1 = r[3]
        ai.rot2 = r[4]
        ai.rot3 = r[5]
        return ai
        
        

In [ ]:
mask1 = fabio.open("deviation-mask.edf").data
mask2 = fabio.open("minimum-mask.edf").data
mask = numpy.logical_or(mask1, mask2)
pil = pyFAI.detector_factory("Pilatus100k")
pil.mask = mask
img = fabio.open("del_65.0_0001p.cbf")
#for k,v in img.header.items(): print(k, v)
    
LaB6 = pyFAI.calibrant.ALL_CALIBRANTS("LaB6")
wavelength = 0.7749e-10
LaB6.wavelength = wavelength

In [ ]:
mgr = MultiGeometryRefinement()
ponis = glob.glob("*.poni")
ponis.sort()
print(ponis)
for fn in ponis:
    base = os.path.splitext(fn)[0]
    ai = pyFAI.load(fn)
    dic = ai.getPyFAI()
    dic["detector"] = pil
    dic["calibrant"] = LaB6
    dic["wavelength"] = LaB6.wavelength
    controlpoints=ControlPoints(base+".npt")
    gr = GeometryRefinement(controlpoints.getList(), **dic)
    mgr.new_geometry(base, image=fabio.open(base+".cbf").data, metadata=base, controlpoints=controlpoints,
                    geometryrefinement= gr, calibrant=LaB6)
print(mgr)
for k,v in mgr.single_geometries.items():
    print(k,v.get_position())

In [ ]:
for lbl, sg in mgr.single_geometries.items():
    print(lbl, sg.geometryrefinement.chi2(), numpy.unique(sg.geometryrefinement.data[:,2]))
    print(sg.geometryrefinement)
    sg.display()

In [ ]:
print(mgr.chi2())
mgr.refine2()
print(mgr.multiparam)
print(mgr.bounds)
#mgr.bounds[3] = (-0.1, 0.1)
#mgr.bounds[4] = (-0.1, 0.1)
#mgr.bounds[5] = (-0.9, 1.1)
#mgr.refine2()


In [ ]:
print(mgr.multiparam)
print(mgr.bounds)
mgr.bounds[3] = -0.01, 0.01
mgr.refine2()

In [ ]:
print(mgr.multiparam)
print(mgr.bounds)
mgr.bounds[4] = -1, 1
mgr.refine2()

In [ ]:
print(mgr.multiparam)
print(mgr.bounds)
mgr.bounds[5] = 0.9, 1.1
mgr.refine2()

In [ ]:
#Re-extrace all control points:
for lbl, sg in mgr.single_geometries.items():
    sg.extract_cp(pts_per_deg=3)
    print(sg.controlpoints)
    sg.geometryrefinement.data = numpy.asarray(sg.controlpoints.getList(),"float64")
    print(sg.geometryrefinement.chi2())
    #sg.geometryrefinement.refine2()
    f=sg.display()


In [ ]:
mgr.refine2()

In [ ]:
#mgr.bounds[0] = 

In [ ]:
#Add one file:
fn = "del_37.0_0001p.cbf"
lbl = os.path.splitext(fn)[0]
print(lbl)
img = fabio.open(fn).data
sg = mgr.new_geometry(lbl, image=img, metadata=lbl, calibrant=LaB6)
ai = mgr.get_poni("del_35.0_0001p", sg.get_position())
dic = ai.getPyFAI()
dic["detector"] = pil
dic["calibrant"] = LaB6
dic["wavelength"] = LaB6.wavelength
gr = GeometryRefinement(numpy.zeros((1,3)), **dic)
sg.geometryrefinement = gr
cp = sg.extract_cp(pts_per_deg=3)
gr.data = numpy.asarray(cp.getList(),"float64")
f = sg.display()
mgr.chi2()
mgr.refine2()


In [ ]:
#Add all the other images:
import glob, os
fnames = glob.glob("*.cbf")
fnames.sort()
for fn in fnames:
    lbl = os.path.splitext(fn)[0]
    if lbl in mgr.single_geometries:
        continue
    print(lbl)
    img = fabio.open(fn).data
    sg = mgr.new_geometry(lbl, image=img, metadata=lbl, calibrant=LaB6)
    sg = mgr.single_geometries[lbl]
    ai = mgr.get_poni("del_35.0_0001p", sg.get_position())
    dic = ai.getPyFAI()
    dic["detector"] = pil
    dic["calibrant"] = LaB6
    dic["wavelength"] = LaB6.wavelength
    gr = GeometryRefinement([[0,0,0]], **dic)
    sg.geometryrefinement = gr
    cp = sg.extract_cp(pts_per_deg=1)
    gr.data = numpy.asarray(cp.getList(),"float64")
    #sg.display()
    

In [ ]:

#Remove images with no rings
print(mgr)
for lbl,sg in mgr.single_geometries.items():
    print(lbl, sg.geometryrefinement.data.shape)
#    if len(sg.controlpoints.getList()) == 0:
#        print("remove", lbl, sg.controlpoints)
#        mgr.single_geometries.pop(lbl)
#print(mgr.chi2())
#mgr.refine2()

In [ ]:
print(mgr)
print(mgr.chi2())
mgr.refine2()

In [ ]:
for lbl,sg in mgr.single_geometries.items():
    print(lbl, sg.geometryrefinement.data.shape)
    sg.extract_cp(pts_per_deg=3)

mgr.bounds[3]=(-0.01,0.01)
mgr.bounds[4]=(-5,5)
mgr.multiparam[1] = 0.015
mgr.multiparam[2] = 0.04042697
mgr.multiparam[3] = -0.00731954
mgr.multiparam[4] = 0.00255093
mgr.refine2()

In [ ]:
mgr.bounds[3]=(-0.01,0.01)
mgr.bounds[4]=(-0.05,0.005)
mgr.multiparam[1] = 0.015
mgr.multiparam[2] = 0.04042697
mgr.multiparam[3] = -0.00731954
mgr.multiparam[4] = 0.00255093
mgr.refine2()

In [ ]:
from pyFAI.multi_geometry  import MultiGeometry
mg = MultiGeometry([ mgr.get_poni(lbl, sg.get_position()) for lbl, sg in mgr.single_geometries.items()], radial_range=(4,75))
print(mg)

In [ ]:
print(mgr.multiparam)
images = [i.image for i in mgr.single_geometries.values()]
figure()
res = mg.integrate1d(images, 30000, polarization_factor=1, error_model="poisson")
errorbar(*res)
xlabel(r"$2\theta$ ($^o$)")

numpy.savetxt("integrated_2theta.dat", numpy.vstack(res).T)


In [ ]:
figure()
imshow(numpy.arcsinh(mg.integrate2d(images, 1000, 360, polarization_factor=1)[0]))